In [394]:
import altair as alt
import pandas as pd

Get data from https://github.com/nytimes/covid-19-data

In [444]:
data = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv')
data = data[data['cases'] > 0]
data = data.sort_values(['state', 'date'])

Calculate number of days since first case `case-days` and first death `death-days`, as well as % day to day increment of cases `case-inc` and deaths `death-inc`.

In [491]:
data['case-days'] = data['cases'].mask(data['cases'] > 0, 1)
data['case-days'] = data.groupby(['state'])['case-days'].cumsum()

data['death-days'] = data['deaths'].mask(data['deaths'] > 0, 1)
data['death-days'] = data.groupby(['state'])['death-days'].cumsum()

data[['case-inc', 'death-inc']] = data.groupby(['state'])[['cases', 'deaths']].pct_change().round(2)

cases = data[data['cases'] > 0]
deaths = data[data['deaths'] > 0]

Plot number of deaths for each state relative to the first death date, line thickness proportional to the % increase

In [486]:
chart = alt.Chart(deaths).encode(
    alt.X('death-days:Q'),
    alt.Y('deaths:Q', scale=alt.Scale(type='symlog')),
    color='state:N')

trail = chart.mark_trail().encode(
    size=alt.Size('death-inc:Q', scale=alt.Scale(type='symlog', domain=[0, 0.75])),
    )

points = chart.mark_circle(size=10).encode(
    tooltip=[
        alt.Tooltip('state:N', title='state'),
        alt.Tooltip('date:T', title='date'),
        alt.Tooltip('deaths:Q', title='deaths'),
        alt.Tooltip('death-inc:Q', title='increment', format='.0%'),
    ])

trail + points

alt.LayerChart(...)

In [494]:
alt.Chart(deaths).mark_rect().encode(
    alt.X('date(date):T'),
    alt.Y('state:N'),
    alt.Color('death-inc:Q',
              scale=alt.Scale(type='symlog', domain=[0, 1]),
              legend=alt.Legend(format='%')),
    tooltip=[
        alt.Tooltip('date:T', title='date'),
        alt.Tooltip('deaths:Q', title='deaths'),
        alt.Tooltip('death-inc:Q', title='increment', format='.0%'),
    ])

alt.Chart(...)

In [510]:
charts = None

for state in data['state'].unique():
    chart = alt.Chart(
        deaths[deaths['state'] != state]
    ).encode(
        alt.X('death-days:Q'),
        alt.Y('deaths:Q', scale=alt.Scale(type='symlog')),
        color=alt.Color('state:N')
    )

    lines = chart.mark_line(size=0.5)
    
    points = chart.mark_circle(size=5).encode(
        tooltip=[
            alt.Tooltip('state:N', title='state'),
            alt.Tooltip('date:T', title='date'),
            alt.Tooltip('deaths:Q', title='deaths'),
            alt.Tooltip('death-inc:Q', title='increment', format='.0%'),
        ])

    other = lines + points

    chart = alt.Chart(deaths[deaths['state'] == state], title=state).encode(
        alt.X('death-days:Q'),
        alt.Y('deaths:Q', scale=alt.Scale(type='symlog')),
        color='state:N')

    trail = chart.mark_trail().encode(
        size=alt.Size('death-inc:Q', scale=alt.Scale(type='symlog', domain=[0, 0.75])),
        )

    points = chart.mark_circle(size=20).encode(
        tooltip=[
            alt.Tooltip('state:N', title='state'),
            alt.Tooltip('date:T', title='date'),
            alt.Tooltip('deaths:Q', title='deaths'),
            alt.Tooltip('death-inc:Q', title='increment', format='.0%'),
        ])
    
    this = trail + points

    if charts is None:
        charts = other + this
    else:
        charts &= other + this

charts

alt.VConcatChart(...)